# Managing Learning Data through Federated Queries on Knowledge Graphs

## Introduction

In recent years, Learning Management Systems (LMSs) have become increasingly important in online education due to their flexible integration platforms for organizing vast learning resources and establishing effective communication channels between teachers and learners. These online platforms are attracting a growing number of users who continually access, download/upload resources, and interact with each other during their teaching/learning processes. This trend has been accelerated by the outbreak of COVID-19.

In this context, academic institutions are generating large volumes of learning-related data that can be analyzed to support teachers in lesson planning, course and faculty degree planning, and university strategic level administration. However, managing such a significant amount of data, which often comes from multiple heterogeneous sources and with attributes that sometimes reflect semantic inconsistencies, poses an emerging challenge.

## Challenge

The primary aim of this use case is to provide artificial intelligence algorithms with the ability to analyze implicit interaction patterns within LMSs registered by a specific e-learning community. To achieve this, we require federated SPARQL queries to obtain data on student interactions and academic performance efficiently, which can be used to feed predictive models and visualizations.

## Datasets

 - **Open University datasets**
The anonymised Open University Learning Analytics Datasets (OULAD) contain data about courses, students and their interactions with Virtual Learning Environment (VLE) for seven selected courses (called modules). Presentations of courses start in February and October - they are marked by “B” and “J” respectively. This datasets contain data of the interactions of 32,593 students in 22 courses, 10,655,280 log records, 173,913 submissions and 206 assignments. They also consider demographic information, as well as interaction records of the students with the materials and grades, both of the assignments and of the final grade of the course.
OULAD data are stored in two different RDF repositories. 
   1. student-oulad dataset: Contains data about students' activities and demographic information.

      SPARQL Endpoint: https://student-oulad.khaos.uma.es/sparql
   2. module-oulad dataset: Contains information about courses and assessments.

      SPARQL Endpoint: https://module-oulad.khaos.uma.es/sparql
     
  Source files: https://khaos.uma.es/movilidad/oulad/
     
  These two RDF repositories are built according to the same OWL ontology. 
  
  Ontology: https://ontologies.khaos.uma.es/oulad


 - **Malaga University Dataset (MUD)**
The MUD datasets consist of data from the Moodle source dataset of the University of Malaga, specifically regarding the Software Engineering degree. These anonymized data are used for the first time in this study and include information on the interactions carried out by users on this LMS platform. The datasets include data from 8524 students across 93 courses, with 1,235,063 log records, 1342 assignments, and 28,270 submissions. These data will be used to support the study's objectives.
MUD data are stored in three different RDF repositories. 

   1. user-mud dataset: Contains data about students, courses, and enrollments.

      SPARQL Enpoint: https://user-mud.khaos.uma.es/sparql
   2. assignment-mud dataset: Contains information about assignments and submissions. 

      SPARQL Enpoint: https://assignment-mud.khaos.uma.es/sparql
   3. log-mud dataset: Contains information about the interactions carried out by students on the LMS platform.

      SPARQL Enpoint: https://log-mud.khaos.uma.es/sparql
     
  Source files: https://khaos.uma.es/movilidad/oulad/
     
  These three RDF repositories are built according to the same OWL ontology.

  Ontology: https://ontologies.khaos.uma.es/e-lion

[Backup of datasets and ontologies](https://uma365-my.sharepoint.com/:f:/g/personal/manuelpaneque_uma_es/ElqOzqf_8AlNpAW9owoo-_wB2o6LkEBvnJ3JnsLg5wwPfQ) 


   
## Analytics case study

The main objective of this study is to train a machine learning algorithm capable of predicting student grades. To do this, we need to generate a dataframe that includes the following features: `user_id`, `course_id`, `diff_days`, `weight_score`, `num_submissions`, and `sum_click`. All students in the OULAD datasets contain this information.  The algorithm must predict the grade of MUD students based on the available data.

## Federated Queries 

We need to define several SPARQL queries to achieve the proposed analytic use case. The following [link](https://colab.research.google.com/drive/1R9BmNzLidU00yhQVnfr2WF7jL-AaO-15?usp=sharing) describes the analytical process to predict the students' grades. You should specify the queries and write them in the corresponding cell.

----------------------------------------------------------


## Install requiered packages

In [2]:
!pip install auto-sklearn PipelineProfiler sparqlwrapper plotly-express

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 21.0 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 881.1/881.1 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.8/23.8 MB 35.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 260.9/260.9 kB 21.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.8/4.8 MB 88.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.5/4.5 MB 90.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 528.1/528.1 kB 44.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.7/41.7 kB 5.3 MB/s eta 0:00:00
  

## Import necessary libraries



In [3]:
from SPARQLWrapper import SPARQLWrapper, CSV
import pandas as pd
from io import BytesIO

for _ in range(3):
    try:
        import autosklearn.classification
        break
    except:
        pass
else:
    raise ImportError("failed to import from autosklearn")

#Data extraction from OULAD datasets

In [7]:
import requests
requests.packages.urllib3.disable_warnings()

import ssl

try:
    _create_unverified_https_context = ssl._create_unverified_context
except AttributeError:
    # Legacy Python that doesn't verify HTTPS certificates by default
    pass
else:
    # Handle target environment that doesn't support HTTPS verification
    ssl._create_default_https_context = _create_unverified_https_context

### Function that executes a SPARQL query on an endpoint and returns the result in a pandas dataframe.

In [11]:
def execute_query(query:str, repository: str="federation"):
    sparql = SPARQLWrapper("https://ec2-54-221-48-173.compute-1.amazonaws.com/sparql")
    sparql.addCustomParameter("repository", repository)
    sparql.setCredentials("admin", "i-0f47f689ca7184940")
    sparql.setQuery(query)
    sparql.setReturnFormat(CSV)
    results = sparql.query().convert()
    return pd.read_csv(BytesIO(results))

## Query 1: Number of clicks made by user_id, code_module and code_presentation.

In [9]:
views_oulad = execute_query("""
PREFIX Repository: <http://www.metaphacts.com/ontologies/repository#>
PREFIX oulad: <https://ontologies.khaos.uma.es/oulad/>
SELECT ?code_module ?code_presentation ?user_id (SUM(?click) AS ?sum_clicks) WHERE {
    ?vle oulad:vle_has_course ?course.
    ?course oulad:code_module ?code_module.
    ?course oulad:code_presentation ?code_presentation.
    
    ?student_vle oulad:student_vle_has_vle ?vle.
    ?student_vle oulad:sum_click ?click.
    ?student_vle oulad:student_vle_has_student_info ?student_info.
    ?student_info oulad:id_student ?user_id.
  
} GROUP BY ?code_module ?code_presentation ?user_id
""")
views_oulad = views_oulad.set_index(['user_id','code_module', 'code_presentation'])
views_oulad

sum_clicks
user_id code_module code_presentation            
281261  CCC         2014B                     463
564632  FFF         2014B                    3483
87322   FFF         2014J                    1408
631492  BBB         2014B                     361
596208  GGG         2013J                     337
...                                           ...
1338955 GGG         2014B                       7
344451  FFF         2014B                    1726
682041  CCC         2014J                       3
592093  DDD         2013J                     395
67505   DDD         2013J                     611

[29228 rows x 1 columns]

## Query 2: Number of submissions made by user_id, code_module and code_presentation.

In [10]:
num_submissions_oulad = execute_query("""
PREFIX oulad: <https://ontologies.khaos.uma.es/oulad/>
SELECT ?code_module ?code_presentation ?user_id (COUNT(?student_assessment) AS ?num_submissions)
WHERE{
    ?course a oulad:Courses .
    ?course oulad:code_module ?code_module.
    ?course oulad:code_presentation ?code_presentation.
    ?assessment oulad:assessment_has_course ?course .
  
  ?student_assessment oulad:student_assessment_has_assessment ?assessment.
  ?student_assessment oulad:student_assessment_has_student ?student_info .
  ?student_info oulad:id_student ?user_id.
} GROUP BY ?code_module ?code_presentation ?user_id
""")
num_submissions_oulad = num_submissions_oulad.set_index(['user_id','code_module', 'code_presentation'])
num_submissions_oulad

num_submissions
user_id code_module code_presentation                 
594246  EEE         2013J                            3
533077  BBB         2014B                            8
295893  FFF         2014J                            2
633666  GGG         2014B                            8
643542  DDD         2014J                            1
...                                                ...
602470  GGG         2013J                            9
401824  FFF         2013J                            2
594470  FFF         2013J                            1
2162388 DDD         2014B                            3
641696  CCC         2014J                            9

[25843 rows x 1 columns]

## Query 3: The difference in days between the final submission date and the student submission date. For each student and course, the difference in the days of all their assignments will be added up.

In [12]:
# note: cannot be executed in federation due to custom function
diff_days_oulad = execute_query("""
PREFIX oulad: <https://ontologies.khaos.uma.es/oulad/>
PREFIX bif: <http://www.openlinksw.com/schemas/bif#>
SELECT ?code_module ?code_presentation ?user_id (SUM(?diff_days_internal) AS ?diff_days)
WHERE{
  SERVICE <https://module-oulad.khaos.uma.es/sparql> {
  	?course a oulad:Courses .
  	?course oulad:code_module ?code_module.
  	?course oulad:code_presentation ?code_presentation.
    ?assessment oulad:assessment_has_course ?course .
    ?assessment oulad:date ?final_submission_date .
  }
  ?student_assessment oulad:student_assessment_has_assessment ?assessment.
  ?student_assessment oulad:student_assessment_has_student ?student_info .
  ?student_assessment oulad:date_submitted ?date_submitted .
  ?student_info oulad:id_student ?user_id.
  BIND( (bif:datediff('day', ?final_submission_date, ?date_submitted)) AS ?diff_days_internal) 
  
} GROUP BY ?code_module ?code_presentation ?user_id
""", "student-oulad")
diff_days_oulad = diff_days_oulad.set_index(['user_id', 'code_module','code_presentation'])
diff_days_oulad

diff_days
user_id code_module code_presentation           
627886  FFF         2014B                   -273
628972  FFF         2014B                   -464
629739  FFF         2014B                   -118
631083  FFF         2014B                      0
105939  FFF         2014J                   -320
...                                          ...
468927  DDD         2013J                    -26
479977  DDD         2013J                    -36
489209  DDD         2013J                    -34
493876  DDD         2013J                      5
497809  DDD         2013J                      8

[25843 rows x 1 columns]

## Query 4: Weight score by user_id, code_module and code_presentation. Take into account only the assessment having a weight less than 100.

In [13]:
weight_score_oulad = execute_query("""
PREFIX oulad: <https://ontologies.khaos.uma.es/oulad/>
SELECT ?code_module ?code_presentation ?user_id (SUM(?weight*?score)/1000 AS ?weight_score)
WHERE{
  	?course a oulad:Courses .
  	?course oulad:code_module ?code_module.
  	?course oulad:code_presentation ?code_presentation.
    ?assessment oulad:assessment_has_course ?course .
    ?assessment oulad:weight ?weight .
    FILTER (?weight < 100)
  
  ?student_assessment oulad:student_assessment_has_assessment ?assessment.
  ?student_assessment oulad:student_assessment_has_student ?student_info .
  ?student_assessment oulad:score ?score .
  ?student_info oulad:id_student ?user_id.
} GROUP BY ?code_module ?code_presentation ?user_id
""")

weight_score_oulad = weight_score_oulad.set_index(['user_id', 'code_module', 'code_presentation'])
weight_score_oulad

weight_score
user_id code_module code_presentation              
570031  BBB         2014B                     8.150
2432551 BBB         2014J                     4.250
531027  BBB         2013B                     0.400
690298  DDD         2014J                     0.325
527991  FFF         2013B                     3.708
...                                             ...
620128  BBB         2014B                     6.868
486836  EEE         2014B                     8.312
446324  EEE         2013J                     9.296
613133  EEE         2014B                     9.188
546722  DDD         2013J                     8.693

[25816 rows x 1 columns]

## Merge features into a single data frame.

In [14]:
features_target_oulad = pd.merge(weight_score_oulad, num_submissions_oulad, left_index=True, right_index=True, how='outer')
features_target_oulad = pd.merge(features_target_oulad, views_oulad, left_index=True, right_index=True, how='outer')
features_target_oulad = pd.merge(features_target_oulad, diff_days_oulad, left_index=True, right_index=True, how='outer')
features_target_oulad = features_target_oulad.fillna(0)
features_target_oulad

weight_score  num_submissions  \
user_id code_module code_presentation                                  
6516    AAA         2014J                     6.350              5.0   
8462    DDD         2013J                     3.405              3.0   
                    2014J                     4.300              4.0   
11391   AAA         2013J                     8.240              5.0   
23629   BBB         2013B                     1.669              4.0   
...                                             ...              ...   
2698257 AAA         2013J                     6.940              5.0   
2698535 CCC         2014B                     0.937              4.0   
        EEE         2013J                     5.344              4.0   
2698577 BBB         2014J                     5.580              5.0   
2698588 BBB         2014J                     9.240              5.0   

                                       sum_clicks  diff_days  
user_id code_module code_presentation                         
6516    AAA         2014J                  1815.0      -13.0  
8462    DDD         2013J                   456.0       -1.0  
                    2014J                     9.0     -238.0  
11391   AAA         2013J                   801.0       -9.0  
23629   BBB         2013B                   108.0       14.0  
...                                           ...        ...  
2698257 AAA         2013J                   486.0       10.0  
2698535 CCC         2014B                   593.0        6.0  
        EEE         2013J                  1741.0        9.0  
2698577 BBB         2014J                   544.0       -5.0  
2698588 BBB         2014J                   411.0       -2.0  

[29278 rows x 4 columns]

## Plot the raw data.

In [15]:
import plotly.express as px
fig = px.scatter_3d(features_target_oulad, x='num_submissions', y='sum_clicks', z='diff_days',
              color='weight_score')
fig.show()

## Categorize the weight_score in two classes.

In [16]:
bins = [-100, 4.9, 11]
labels=['fail', 'pass']
features_target_oulad['grade'] = pd.cut(features_target_oulad['weight_score'], bins, labels=labels)
features_target_oulad = features_target_oulad[['num_submissions', 'sum_clicks','diff_days', 'grade']]
features_target_oulad

num_submissions  sum_clicks  diff_days  \
user_id code_module code_presentation                                           
6516    AAA         2014J                          5.0      1815.0      -13.0   
8462    DDD         2013J                          3.0       456.0       -1.0   
                    2014J                          4.0         9.0     -238.0   
11391   AAA         2013J                          5.0       801.0       -9.0   
23629   BBB         2013B                          4.0       108.0       14.0   
...                                                ...         ...        ...   
2698257 AAA         2013J                          5.0       486.0       10.0   
2698535 CCC         2014B                          4.0       593.0        6.0   
        EEE         2013J                          4.0      1741.0        9.0   
2698577 BBB         2014J                          5.0       544.0       -5.0   
2698588 BBB         2014J                          5.0       411.0       -2.0   

                                      grade  
user_id code_module code_presentation        
6516    AAA         2014J              pass  
8462    DDD         2013J              fail  
                    2014J              fail  
11391   AAA         2013J              pass  
23629   BBB         2013B              fail  
...                                     ...  
2698257 AAA         2013J              pass  
2698535 CCC         2014B              fail  
        EEE         2013J              pass  
2698577 BBB         2014J              pass  
2698588 BBB         2014J              pass  

[29278 rows x 4 columns]

## Plot the categorized grades.

In [17]:
fig = px.scatter_3d(features_target_oulad, x='num_submissions', y='sum_clicks', z='diff_days',
              color='grade')
fig.show()

## Split the data into features and target.

In [18]:
import numpy as np
X = features_target_oulad[['num_submissions', 'sum_clicks','diff_days']]
y = features_target_oulad.grade.reset_index(drop=True).values
y = np.array(y)

## Split the data into test and train.

In [19]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25, random_state=1)

## Train the model.

In [20]:
import autosklearn.classification
model = autosklearn.classification.AutoSklearnClassifier(time_left_for_this_task=600)
model.fit(X_train, y_train)
predictions = model.predict(X_test)

## Training models report.

In [21]:
import PipelineProfiler
profiler_data = PipelineProfiler.import_autosklearn(model)
PipelineProfiler.plot_pipeline_matrix(profiler_data)

## Classification report on test data.

In [22]:
from sklearn.metrics import classification_report
print("% Accuracy: " + str(100 - (100 * sum(predictions != y_test)/len(y_test))), '%')
print(classification_report(y_test, predictions))

% Accuracy: 91.01092896174863 %
              precision    recall  f1-score   support

        fail       0.94      0.88      0.91      3776
        pass       0.88      0.94      0.91      3544

    accuracy                           0.91      7320
   macro avg       0.91      0.91      0.91      7320
weighted avg       0.91      0.91      0.91      7320



# Data extraction from MUD datasets

### Function that executes a SPARQL query on an endpoint and returns the result in a pandas dataframe.

In [25]:
def execute_query(query:str, repository: str="federation"):
    sparql = SPARQLWrapper("https://ec2-54-221-48-173.compute-1.amazonaws.com/sparql")
    sparql.addCustomParameter("repository", repository)
    sparql.setCredentials("admin", "i-0f47f689ca7184940")
    sparql.setQuery(query)
    sparql.setReturnFormat(CSV)
    results = sparql.query().convert()
    return pd.read_csv(BytesIO(results))

## Query 5: Number of clicks made by a student in each course in which he/she is enrolled.

In [26]:
views_mud = execute_query("""
PREFIX e-lion: <http://ontologies.khaos.uma.es/e-lion/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
SELECT (SUM(?numclick) AS ?sum_clicks) ?user_id ?course_id
WHERE{
   
   ?user rdf:type e-lion:User.
   ?user e-lion:userId ?user_id.
   ?user e-lion:isEnrolled ?enroll.
   ?enroll e-lion:inCourse ?course.
   ?course rdf:type e-lion:Course.
   ?course e-lion:courseId ?course_id.
 
 ?x e-lion:logAction ?action. FILTER (str(?action) = "viewed"^^xsd:string)
 ?x e-lion:logEduLevel ?edulevel.FILTER (?edulevel = 2)
 ?x e-lion:recordUser ?user.
 ?x e-lion:recordCourse ?course.
 ?x e-lion:logSumClick ?numclick.
}GROUP BY ?user_id ?course_id
""")
views_mud=views_mud.set_index(['user_id','course_id'])
views_mud

sum_clicks
user_id course_id            
12148   22                110
12133   36                117
13436   23                154
315     36                219
13818   17                  8
...                       ...
4827    19                  4
319     23                118
13642   85                 21
2293    36                 80
8356    57                202

[7178 rows x 1 columns]

## Query 6: Number of submissions made by a student in each course in which he/she is enrolled.

In [27]:
subs_mud = execute_query("""
PREFIX e-lion: <http://ontologies.khaos.uma.es/e-lion/>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
SELECT (COUNT(?submission) AS ?num_submissions) ?user_id ?course_id
WHERE{
     ?user rdf:type e-lion:User.
     ?user e-lion:userId ?user_id.
     ?user e-lion:isEnrolled ?enroll.
     ?enroll e-lion:inCourse ?course.
     ?course rdf:type e-lion:Course.
     ?course e-lion:courseId ?course_id.
   
     ?submission e-lion:belongsUser ?user.
     ?submission e-lion:belongAssignment ?assigment.
     ?assigment e-lion:hasCourse ?course.
   
}GROUP BY ?user_id ?course_id
""")
subs_mud=subs_mud.set_index(['user_id','course_id'])
subs_mud

num_submissions
user_id course_id                 
12400   73                       1
5433    27                       2
6792    79                       1
10698   85                       2
1064    38                       1
...                            ...
12265   79                       1
7103    73                       3
7101    75                       4
9772    87                       4
8428    66                       1

[4739 rows x 1 columns]

## Query 7: Sum of diff days between the assignment date and submission date by user_id and course_id.

In [28]:
# note: cannot be executed in federation due to proprietary virtuoso function
diff_days_mud = execute_query("""
PREFIX e-lion: <http://ontologies.khaos.uma.es/e-lion/>
PREFIX bif: <http://www.openlinksw.com/schemas/bif#>
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
SELECT (SUM(?diff_days) AS ?diff_days) ?user_id ?course_id
WHERE{
   SERVICE <https://user-mud.khaos.uma.es/sparql> {
     ?user rdf:type e-lion:User.
     ?user e-lion:userId ?user_id.
     ?user e-lion:isEnrolled ?enroll.
     ?enroll e-lion:inCourse ?course.
     ?course rdf:type e-lion:Course.
     ?course e-lion:courseId ?course_id.
 }
 SERVICE <https://assignment-mud.khaos.uma.es/sparql> {
     ?assigment e-lion:hasCourse ?course.
     ?assigment e-lion:assignmentDueDate ?duedate.
     ?submission e-lion:belongAssignment ?assigment.
     ?submission e-lion:belongsUser ?user.
     ?submission e-lion:submissionTimeCreated ?timecreated.
     BIND (bif:datediff("day", ?duedate, ?timecreated) AS ?diff_days)
 }
}GROUP BY ?user_id ?course_id
""", "log-mud")
diff_days_mud=diff_days_mud.set_index(['user_id','course_id'])
diff_days_mud

diff_days
user_id course_id           
871     73              -138
156     75             17539
14998   15                -3
9550    38                -7
5682    66             17661
...                      ...
4786    38                -7
6396    78             70236
10402   38                -7
15782   78             70236
10383   89                 0

[4739 rows x 1 columns]

## Merge features into a single data frame.

In [29]:
features_mud = pd.merge(subs_mud, diff_days_mud, left_index=True, right_index=True, how='outer')
features_mud = pd.merge(views_mud, features_mud, left_index=True, right_index=True, how='outer')
features_mud = features_mud.fillna(0)
features_mud = features_mud[['num_submissions', 'sum_clicks','diff_days']]
features_mud

num_submissions  sum_clicks  diff_days
user_id course_id                                        
8       16                     2.0        62.0    17540.0
        20                     2.0        41.0       27.0
        31                     0.0        97.0        0.0
        58                    15.0        89.0    35877.0
        66                    11.0       187.0    17583.0
...                            ...         ...        ...
15846   73                     4.0       114.0     -389.0
        78                     5.0      1178.0    70235.0
        84                    11.0      1060.0    87655.0
        85                     0.0        38.0        0.0
        89                    10.0        94.0       -1.0

[7739 rows x 3 columns]

## Predict grades with the model.

In [30]:
y_pred=model.predict(features_mud)
features_mud["grade"] = y_pred
features_mud

num_submissions  sum_clicks  diff_days grade
user_id course_id                                              
8       16                     2.0        62.0    17540.0  fail
        20                     2.0        41.0       27.0  fail
        31                     0.0        97.0        0.0  fail
        58                    15.0        89.0    35877.0  pass
        66                    11.0       187.0    17583.0  pass
...                            ...         ...        ...   ...
15846   73                     4.0       114.0     -389.0  fail
        78                     5.0      1178.0    70235.0  fail
        84                    11.0      1060.0    87655.0  pass
        85                     0.0        38.0        0.0  fail
        89                    10.0        94.0       -1.0  pass

[7739 rows x 4 columns]

## Plot the predict grades.

In [31]:
fig = px.scatter_3d(features_mud, x='num_submissions', y='sum_clicks', z='diff_days',
              color='grade')
fig.show()